In [1]:
#Librerias necesarias para implementacion de algoritmo genetico
from __future__ import print_function

from evolver import Evolver

from tqdm import tqdm

import logging

import sys


# Aplicacion del Modelo
Aqui se aplica directamente el modelo descrito implementando el algoritmo genetico

In [2]:
#Librerias necesarias para trabajar con datasets
import pandas as pd
import numpy as np
from sklearn import linear_model, model_selection

#Librerias necesarias para aplicar redes neuronales
import tensorflow as tf
pd.set_option('display.max_columns', None)
df= pd.read_csv("Historial_Alumnos.csv", sep=",",index_col=False)
df.head()

id_anony Cod.Car.Sec  Cod.Car.Sec Codificado  Materia_1  \
0      2838  MCT-PLS13                     28.0  CALCULO 1   
1      4037  MCT-PLS13                     28.0  CALCULO 1   
2      4061  MCT-PLS13                     28.0  CALCULO 1   
3      4062  MCT-PLS13                     28.0  CALCULO 1   
4      4065  MCT-PLS13                     28.0  CALCULO 1   

   Materia_1 codificada  Anho_F_1  ciclo_F_1  Recursante_1  P1_F_1  P2_F_1  \
0                  33.0    2013.0        2.0           1.0     0.0    17.0   
1                  33.0    2015.0        2.0           1.0    16.0    19.0   
2                  33.0    2015.0        2.0           1.0    14.0    27.0   
3                  33.0    2015.0        2.0           1.0     5.0    24.0   
4                  33.0    2015.0        2.0           1.0    19.0    30.0   

   T_F_1  NotaFinal_1  Materia_1 Nota=1  Materia_1 Nota=2  Materia_1 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    8.0          5.0               0.0               0.0               0.0   
2    8.0          3.0               0.0               0.0               1.0   
3    6.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_1 Nota=4  Materia_1 Nota=5  Abandono la Materia 1  Materia_2  \
0               0.0               0.0                    1.0  CALCULO 2   
1               0.0               1.0                    0.0  CALCULO 2   
2               0.0               0.0                    0.0  CALCULO 2   
3               0.0               0.0                    0.0  CALCULO 2   
4               0.0               1.0                    0.0  CALCULO 2   

   Materia_2 codificada  Anho_F_2  ciclo_F_2  Recursante_2  P1_F_2  P2_F_2  \
0                  34.0    2014.0        1.0           1.0    11.0    16.0   
1                  34.0    2016.0        1.0           1.0    22.0    31.0   
2                  34.0    2016.0        1.0           1.0    13.0    23.0   
3                  34.0    2016.0        1.0           1.0    21.0    19.0   
4                  34.0    2016.0        1.0           1.0    24.0    29.0   

   T_F_2  NotaFinal_2  Materia_2 Nota=1  Materia_2 Nota=2  Materia_2 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    7.0          5.0               0.0               0.0               0.0   
2    5.0          2.0               0.0               1.0               0.0   
3    5.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_2 Nota=4  Materia_2 Nota=5  Abandono la Materia 2  Materia_3  \
0               0.0               0.0                    0.0  CALCULO 3   
1               0.0               1.0                    0.0  CALCULO 3   
2               0.0               0.0                    0.0  CALCULO 3   
3               0.0               0.0                    0.0  CALCULO 3   
4               0.0               1.0                    0.0  CALCULO 3   

   Materia_3 codificada  Anho_F_3  ciclo_F_3  Recursante_3  P1_F_3  P2_F_3  \
0                  35.0    2016.0        2.0           1.0    10.0     7.0   
1                  35.0    2016.0        2.0           1.0     6.0     9.0   
2                  35.0    2016.0        2.0           1.0    17.0    10.0   
3                  35.0    2016.0        2.0           1.0     5.0    18.0   
4                  35.0    2016.0        2.0           1.0    22.0    20.0   

   T_F_3  NotaFinal_3  Materia_3 Nota=1  Materia_3 Nota=2  Materia_3 Nota=3  \
0    2.0          2.0               0.0               1.0               0.0   
1    8.0          4.0               0.0               0.0               0.0   
2    8.0          2.0               0.0               1.0               0.0   
3    6.0          2.0               0.0               1

Antes que nada, es necesario preparar los datos que la red neuronal solicita para poder procesar la opcion mas viable para nuestro analisis

In [3]:
data=df[['Materia_1 codificada','Anho_F_1','ciclo_F_1','Recursante_1','P1_F_1','P2_F_1','T_F_1','NotaFinal_1']]

[filas,columnas]=data.shape
labels=df[['Materia_2 Nota=2']]

#Como labels figura como string, es necesario cambiarlos a valores enteros
data = np.array(data)
labels = np.array(labels)
labels=np.ravel(labels)

#Verificamos las dimensiones de data y labels
display(np.shape(labels))
display(np.shape(data))

(56,)

(56, 8)

Los datos que el algoritmo genetico solicita a lo largo de su procesamiento son data, labels y columnas. Para facilitar dichos datos del notebook al algoritmo genetico, se emplea la libreria pickle

In [4]:
from pickle import dump,load
dump(data, open('data.pkl', 'wb'))
dump(labels, open('labels.pkl', 'wb'))
dump(columnas, open('columnas.pkl', 'wb'))

Una vez definidos apropiadamente estos parametros, se procede a realizar el procesamiento con el algoritmo genetico

In [5]:
import main as ge
lista=ge.main()

07/07/2021 09:45:58 AM - INFO - ***generate(generations, population, all_possible_genes, dataset)***
07/07/2021 09:45:58 AM - INFO - ***Now in generation 1 of 50***
07/07/2021 09:45:58 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 09:45:58 AM - INFO - {'nb_layers': 2, 'activation': 'relu', 'optimizer': 'adamax', 'nb_neurons': [64, 32, 16, 16, 32, 64]}
07/07/2021 09:45:58 AM - INFO - Acc: 0.00%
07/07/2021 09:45:58 AM - INFO - UniID: 1
07/07/2021 09:45:58 AM - INFO - Mom and Dad: 0 0
07/07/2021 09:45:58 AM - INFO - Gen: 1
07/07/2021 09:45:58 AM - INFO - Hash: aba43b1ad0a95989fa79967923ec1e7e
07/07/2021 09:45:58 AM - INFO - {'nb_layers': 5, 'activation': 'relu', 'optimizer': 'adamax', 'nb_neurons': [32, 128, 64, 16, 128, 32]}
07/07/2021 09:45:58 AM - INFO - Acc: 0.00%
07/07/2021 09:45:58 AM - INFO - UniID: 2
07/07/2021 09:45:58 AM - INFO - Mom and Dad: 0 0
07/07/2021 09:45:58 AM - INFO - Gen: 1
07/07/2021 09:45:58 AM - INFO - Hash:

07/07/2021 09:45:58 AM - INFO - {'nb_layers': 4, 'activation': 'relu', 'optimizer': 'adam', 'nb_neurons': [128, 64, 32, 128, 16, 16]}
07/07/2021 09:45:58 AM - INFO - Acc: 0.00%
07/07/2021 09:45:58 AM - INFO - UniID: 22
07/07/2021 09:45:58 AM - INFO - Mom and Dad: 0 0
07/07/2021 09:45:58 AM - INFO - Gen: 1
07/07/2021 09:45:58 AM - INFO - Hash: 907624b23dc2405bd0c6045e5b6effc6
07/07/2021 09:45:58 AM - INFO - {'nb_layers': 2, 'activation': 'relu', 'optimizer': 'adam', 'nb_neurons': [16, 16, 32, 32, 64, 64]}
07/07/2021 09:45:58 AM - INFO - Acc: 0.00%
07/07/2021 09:45:58 AM - INFO - UniID: 23
07/07/2021 09:45:58 AM - INFO - Mom and Dad: 0 0
07/07/2021 09:45:58 AM - INFO - Gen: 1
07/07/2021 09:45:58 AM - INFO - Hash: 104da175c5e0380b4ac85fff7ba63c6b
07/07/2021 09:45:58 AM - INFO - {'nb_layers': 3, 'activation': 'sigmoid', 'optimizer': 'adamax', 'nb_neurons': [32, 64, 16, 16, 32, 64]}
07/07/2021 09:45:58 AM - INFO - Acc: 0.00%
07/07/2021 09:45:58 AM - INFO - UniID: 24
07/07/2021 09:45:58 AM -

***Dataset: dataset
***Evolving for 50 generations with population size = 30***
(44,)
(44, 8)
(44, 2)
(44, 8)
(44, 8)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 161ms/step - loss: 0.7298 - accuracy: 0.3864 - val_loss: 0.7077 - val_accuracy: 0.0833
Epoch 2/50
1/1 [==============================] - 0s 13ms/step - loss: 0.7193 - accuracy: 0.4091 - val_loss: 0.6935 - val_accuracy: 0.5833
Epoch 3/50
1/1 [==============================] - 0s 11ms/step - loss: 0.7123 - accuracy: 0.3864 - val_loss: 0.6815 - val_accuracy: 0.8333


  3%|▎         | 1/30 [00:00<00:28,  1.03it/s]07/07/2021 09:45:59 AM - INFO - Getting Keras datasets
07/07/2021 09:45:59 AM - INFO - Compling Keras model
07/07/2021 09:45:59 AM - INFO - Architecture:[32, 128, 64, 16, 128, 32],relu,adamax,5


Test loss: 0.6814630627632141
Test accuracy: 0.8333333134651184

 Modelo mas eficiente creado 

(44,)
(44, 8)
(44, 2)
(44, 8)
(44, 8)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 131ms/step - loss: 0.6709 - accuracy: 0.6136 - val_loss: 0.6437 - val_accuracy: 0.9167
Epoch 2/50
1/1 [==============================] - 0s 13ms/step - loss: 0.6482 - accuracy: 0.8409 - val_loss: 0.6251 - val_accuracy: 0.9167
Epoch 3/50
1/1 [==============================] - 0s 14ms/step - loss: 0.6381 - accuracy: 0.8409 - val_loss: 0.6082 - val_accuracy: 0.9167
Test loss:

...

 98%|█████████▊| 58/59 [00:36<00:00,  1.54it/s]07/07/2021 10:12:25 AM - INFO - Getting Keras datasets
07/07/2021 10:12:25 AM - INFO - Compling Keras model
07/07/2021 10:12:25 AM - INFO - Architecture:[16, 16, 128, 64, 128, 128],relu,adam,5


Test loss: 1.0813313722610474
Test accuracy: 0.0833333358168602
(44,)
(44, 8)
(44, 2)
(44, 8)
(44, 8)
(44, 2)
Epoch 1/50


07/07/2021 10:12:26 AM - WARNING - 5 out of the last 13 calls to <function Model.make_train_function.<locals>.train_function at 0x000001FD082BA670> triggered tf.function retracing. Tracing is expensive and the excessive number of tracings could be due to (1) creating @tf.function repeatedly in a loop, (2) passing tensors with different shapes, (3) passing Python objects instead of tensors. For (1), please define your @tf.function outside of the loop. For (2), @tf.function has experimental_relax_shapes=True option that relaxes argument shapes that can avoid unnecessary retracing. For (3), please refer to https://www.tensorflow.org/tutorials/customization/performance#python_or_tensor_args and https://www.tensorflow.org/api_docs/python/tf/function for  more details.


1/1 [==============================] - 0s 132ms/step - loss: 0.6962 - accuracy: 0.4318 - val_loss: 0.6849 - val_accuracy: 0.8333
Epoch 2/50
1/1 [==============================] - 0s 13ms/step - loss: 0.6847 - accuracy: 0.7273 - val_loss: 0.6714 - val_accuracy: 0.9167
Epoch 3/50
1/1 [==============================] - 0s 10ms/step - loss: 0.6719 - accuracy: 0.8182 - val_loss: 0.6580 - val_accuracy: 0.9167
Test loss: 0.6579516530036926
Test accuracy: 0.9166666865348816


100%|██████████| 59/59 [00:37<00:00,  1.57it/s]
07/07/2021 10:12:26 AM - INFO - Generation average: 62.29%
07/07/2021 10:12:26 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:12:26 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:12:26 AM - INFO - {'activation': 'relu', 'nb_layers': 2, 'optimizer': 'adam', 'nb_neurons': [16, 64, 16, 16, 128, 128]}
07/07/2021 10:12:26 AM - INFO - Acc: 100.00%
07/07/2021 10:12:26 AM - INFO - UniID: 106
07/07/2021 10:12:26 AM - INFO - Mom and Dad: 3 84
07/07/2021 10:12:26 AM - INFO - Gen: 6
07/07/2021 10:12:26 AM - INFO - Hash: 6c35d8e2769ca641697c7165025310d3
07/07/2021 10:12:26 AM - INFO - {'activation': 'relu', 'nb_layers': 2, 'optimizer': 'adamax', 'nb_neurons': [16, 128, 16, 128, 128, 128]}
07/07/2021 10:12:26 AM - INFO - Acc: 100.00%
07/07/2021 10:12:26 AM - INFO - UniID: 178
07/07/2021 10:12:26 AM - INFO - Mom and Dad: 3 106
07/07/20